# Topic Modeling

Akio Kakishima

### Sources

https://radimrehurek.com/gensim/models/ldaseqmodel.html

https://markroxor.github.io/gensim/static/notebooks/ldaseqmodel.html

https://www.youtube.com/watch?v=7BMsuyBPx90 <-- Dave Blei's Google talk on Dynamic Topic Modelling

https://towardsdatascience.com/exploring-the-un-general-debates-with-dynamic-topic-models-72dc0e307696 

^ Explains why each new paragraph should be treated as a separate document in DTM


### Notes
This .ipynb file runs topic modeling. Make sure to have parsed the PDFs before running this analysis. 

In [71]:
BIGRAMS = False
LOAD_DICTIONARY = True
LOAD_LDA = False
LOAD_DTM = False
num_topics = 50
threshold = 25

In [45]:
from collections import Counter
from gensim import models
from gensim.corpora import Dictionary, bleicorpus
from gensim.models import ldaseqmodel, ldamodel
from gensim.models.wrappers.dtmmodel import DtmModel
from gensim.test.utils import datapath
import pyLDAvis
import matplotlib.pyplot as plt
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer 
import numpy as np
import os
import pandas as pd # ver 0.24.2
import pickle
import re
import time
import winsound

In [46]:
def remove_threshold(input_list, thresh):
    output_set = set()
    c = Counter(input_list)
    for each in c:
        if c[each] <= thresh:
            output_set.add(each)
    return output_set

In [61]:
def preprocess(raw, BIGRAM):
    """
    Takes in a string, lowercases all the text,
    fixes hyphenation, then tokenizes the input. 
    Outputs a list of all the tokens in the input document. 
    Each token is at least 3 chars long. 
    Also removed numbers, and stopwords. 
    Stopwords downloaded from nltk.downloads('stopwords'). 

    Parameters
    ----------
    first : string, or parser 
        `raw` is the pdf document

    Returns
    -------
    list
        A list of each token, stopword filtered

    """

    lowered = raw.lower()
    fixed = re.sub(r'[\-]\W+', '', lowered)
    whitespace = re.sub(r'[\W]+', ' ', fixed)

    tokenizer = RegexpTokenizer(r'[A-z]{4,}')
    additional_list = ['also', 'ndr', 'red', 'crescent', 'cross', 'world', 'disaster', 'report', 'chap', 'page', 'ifrc','unhcr']
    tokenized = [word for word in tokenizer.tokenize(fixed) if word not in additional_list]
    
    
    lemmatizer = WordNetLemmatizer()
    lemmed = [lemmatizer.lemmatize(word) for word in tokenized if word not in stopwords.words('english')]

    remove_set = remove_threshold(lemmed, threshold)
    
    lemmed_filtered = [i for i in lemmed if i not in remove_set]
    
    if BIGRAM:
        bigram = list(nltk.bigrams(lemmed_filtered))
        filtered_words = [i for i in map('_'.join, bigram)]
    else:
        filtered_words = lemmed_filtered
    
    return filtered_words

In [62]:
def extract_para(raw, len_list):
    """
    Input is lowercased, and split by paragraph breaks
    using regex. The number of paragraphs are analyzed
    and appended in input list, 'len_list'
    
    Returns a list, 'list_of_paragraphs', which is the
    output from the split function.

    Parameters
    ----------
    first : string
        text of the PDF file
    second : list
        list to keep track of number of paragraph 
        extracted from input, 'raw'
        
    Returns
    -------
    list

    """

    lowered = raw.lower()
    list_of_paragraphs = re.split(r'\.[ ][\n]+', lowered)
    len_list.append(len(list_of_paragraphs))
    
    return list_of_paragraphs

In [63]:
def determine_year(pdf_title):
    searchObj = re.search(r'20[0-9]{2}|19[0-9]{2}', pdf_title, re.M|re.I)
    if searchObj:
        year = searchObj.group()
    
    return int(year)

In [64]:
def beeper():
    '''
    Beeps when activated
    '''
    
    eighth = 250
    half = 1000
    g = 392 #hz
    ef = 311 #hz

    for i in range(3):
        winsound.Beep(g, eighth)
    winsound.Beep(ef, half)

## Get/Set common_corpus and common_dictionary

In [65]:
%%time

if LOAD_DICTIONARY:
    print("loading Dictionary, corpus, and len documents")
    common_dictionary = Dictionary.load('model/common_dictionary')
    with open('model/common_corpus_pickled', 'rb') as f:
        common_corpus = pickle.load(f)
    with open('model/len_docs_pickled', 'rb') as f:
        lengths_of_docs = pickle.load(f)
    
else:
    print("Dictionary, corpus, and len documents not found; initializing")

    text_library = {}
    list_of_string = []
    list_of_list_of_string = []
    lengths_of_docs = []

    path = "data/"
    dirs = os.listdir(path)
    for each_pdf in dirs:
        if each_pdf == 'WDR-2018-EN-LR.pdf': pass # our testset
        else:
            print(each_pdf)       
            with open('txt/{}.txt'.format(str(each_pdf)), 'r', encoding='utf8') as f:
                text = f.read()
                text_year = determine_year(each_pdf)
                try:
                    text_update = "{}\n{}".format(text_library[text_year], text)
                    text_library.update({text_year: text_update})
                except:
                    text_library[text_year] = text

    for i in sorted(text_library):
        print("year: {}".format(i))
        text = text_library[i]
        list_of_paragraphs = extract_para(text, lengths_of_docs)
        for i in list_of_paragraphs:
            if len(i) > 3:
                list_of_list_of_string.append(preprocess(i, BIGRAMS))
            else: pass

    # Create a corpus from a list of texts
    common_dictionary = Dictionary(list_of_list_of_string)
    common_corpus = [common_dictionary.doc2bow(text) for text in list_of_list_of_string]

    common_dictionary.save('model/common_dictionary')
    with open('model/common_corpus_pickled', 'wb') as f:
        pickle.dump(common_corpus, f)
    with open('model/len_docs_pickled', 'wb') as f:
        pickle.dump(lengths_of_docs, f)

Dictionary, corpus, and len documents not found; initializing
1259900-IFRC Annual Report 2012-EN_LR.pdf
1296700-IFRC Annual Report 2014-EN_LR.pdf
2010_annual_report.pdf
2011 ar_reader_spreads_final.pdf
2012_MC_AR-for-web_0213-2.pdf
2012_WDR_Full_Report.pdf
2016_annual_report.pdf
21400_WDR2001.pdf
32600-WDR_2002.pdf
43800-WDR_2003_En.pdf
58000-WDR2004-LR.pdf
69001-WDR2005-english-LR.pdf
9000-WDR2000.pdf
IFRC Annual Report 2013_FINAL.pdf
IFRC Annual Report 2015-EN_LR.pdf
IFRC-Annual-report-2010-English.pdf
MC_2014_AnnualReport.pdf
MC_AR2017_20pgs_0318_FIN.pdf
Mercy_Corps_2015_Annual_Report.pdf
UNHCR_GT_2010.pdf
UNHCR_GT_2012.pdf
UNHCR_GT_2013.pdf
UNHCR_GT_2014.pdf
UNHCR_GT_2015.pdf
UNHCR_GT_2016.pdf
UNHCR_GT_2017.pdf
WDR 2013 complete.pdf
WDR2006-English-LR.pdf
WDR2007-English.pdf
WDR2008-full.pdf
WDR2009-full.pdf
WDR2010-full.pdf
year: 2000
year: 2001
year: 2002
year: 2003
year: 2004
year: 2005
year: 2006
year: 2007
year: 2008
year: 2009
year: 2010
year: 2011
year: 2012
year: 2013
year:

## NMF

In [66]:
# nmf = models.Nmf(common_corpus, num_topics=10)

## Baseline: LDA

In [67]:
%%time
home = os.getcwd()

if LOAD_LDA:
    print("loading LDAmodel")
    lda = ldamodel.LdaModel.load(os.path.join(home, 'model/LDAmodel_{}'.format(num_topics)))
else:
    for num_topics_sub in [num_topics]:
        print("LDAmodel not found; initializing ldamodel")
        lda = ldamodel.LdaModel(corpus=common_corpus, id2word=common_dictionary, num_topics=num_topics_sub, update_every=1, passes=1)

        print("saving")
        lda.save(os.path.join(home, 'model/LDAmodel_{}'.format(num_topics_sub)))

LDAmodel not found; initializing ldamodel


C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

saving
Wall time: 1.06 s


In [68]:
def pretty_print_topic(n_w = len(common_dictionary.values())):
    epoch = []
    topic_list = []
    topic_imp = []
    
    for idx, each_topic in enumerate(lda.print_topics(num_topics=num_topics, num_words=n_w)):
        # len(common_dictionary.values()) = gets all vocab
        for each_token in each_topic[1].split('+'):
            topic_importance, token = each_token.split("*")
            topic_list.append(re.sub(r'[^A-z0-9]+', '', token))
            topic_imp.append(topic_importance)
            epoch.append(idx)
    data = {'epoch': epoch, 'topic': topic_list, 'topic_importance': topic_imp}
    lda_df = pd.DataFrame.from_dict(data)
#     print(len(lda_df))
#     display(lda_df)
    
    return lda_df

lda_df = pretty_print_topic(n_w = 5)

for each_epoch in lda_df['epoch'].unique():
    display(lda_df[lda_df['epoch'] == each_epoch]['topic'])

0          forced
1         country
2    displacement
3          people
4     development
Name: topic, dtype: object

5     humanitarian
6           people
7    international
8      information
9         disaster
Name: topic, dtype: object

10       radio
11      medium
12      people
13         aid
14    disaster
Name: topic, dtype: object

15          society
16             mail
17         redcross
18             http
19    international
Name: topic, dtype: object

20    humanitarian
21      technology
22          people
23        disaster
24       community
Name: topic, dtype: object

...

225     humanitarian
226           agency
227           people
228         disaster
229    international
Name: topic, dtype: object

230           people
231             risk
232              aid
233         disaster
234    international
Name: topic, dtype: object

235     million
236      people
237        cent
238      locust
239    reported
Name: topic, dtype: object

240          society
241    international
242         disaster
243             mail
244           united
Name: topic, dtype: object

245         disaster
246             loss
247           people
248              aid
249    international
Name: topic, dtype: object

## DTM

In [74]:
%%time
home = os.getcwd()

if LOAD_DTM:
    print("loading DTMmodel")
    ldaseq = ldaseqmodel.LdaSeqModel.load('model/DTMmodel_{}'.format(num_topics))
else:
    for num_topics_sub in [num_topics]:
        print(num_topics)
        print("DTMmodel not found; initializing DTMmodel")
        bc = bleicorpus.BleiCorpus.serialize(fname=os.path.join(home, 'model/blei_{}'.format(num_topics_sub)), corpus=common_corpus)
        ldaseq = ldaseqmodel.LdaSeqModel(corpus=common_corpus, id2word=common_dictionary, time_slice=lengths_of_docs, num_topics=num_topics_sub)
        # ldaseq.print_topics(time=0)

        print("saving")
        ldaseq.save(os.path.join(home, 'model/DTMmodel_{}'.format(num_topics_sub)))

50
DTMmodel not found; initializing DTMmodel


C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

...

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(

C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total))
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:290: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total))
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total))
C:\Users\Akio\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:1472: RuntimeWarning: invalid value encountered in double_scalars
  converged = np.fabs((lhood_old - lhood) / (lhood_old * total)

saving
Wall time: 1h 6min 55s


In [75]:
def output_dtm(as_csv = False):
    '''
    Saves output of DTM as csv
    '''
    if as_csv:
        with open('dtm_output.csv', 'w', newline='') as f:
            csv_writer = csv.writer(f)
            csv_writer.writerow(['topic', 'time', 'term', 'topic_importance'])
            for t in range(len(lengths_of_docs)):
                counter = 0
                for i in ldaseq.print_topics(time=t, top_terms=15):
            #         print(i)
                    counter += 1
                    for j in range(len(i)):
                        csv_writer.writerow([counter,t,i[j][0], i[j][1]])
    else:
        pandas_dict = {}
        counter = 0
        for each_epoch in range(len(lengths_of_docs)):
            for each_topic, i in enumerate(ldaseq.print_topics(time=each_epoch, top_terms=len(common_dictionary.values()))):
                for each_tuple in i:
                    (term, importance) = each_tuple
                    pandas_dict.update({counter: [each_epoch, each_topic, term, importance]})
                    counter += 1
        output_df = pd.DataFrame.from_dict(pandas_dict, orient='index', columns=['epoch', 'topic_number', 'topic_terms', 'topic_importance'])
        return output_df
dtm_df = output_dtm()
dtm_df['id']= dtm_df['topic_terms'].map(common_dictionary.token2id)
dtm_df.head()

epoch  topic_number topic_terms  topic_importance  id
0      0             0        rise           0.96638  40
1      0             0        mail           0.00007   5
2      0             0     society           0.00007   7
3      0             0        http           0.00007   3
4      0             0    redcross           0.00007   6

In [76]:
def display_viz(save = True, time = 0):
    doc_topic, topic_term, doc_lengths, term_frequency, vocab = ldaseq.dtm_vis(time=time, corpus = common_corpus)
    vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
    if save:
        pyLDAvis.save_html(vis_wrapper, 'viz/DTM{}_viz.html'.format(num_topics))
    else: pass
    return pyLDAvis.display(vis_wrapper)

In [77]:
display_viz(time=0)

C:\Users\Akio\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


lambda = 1 results in the familiar ranking of terms in decreasing order of their topic-specific probability, and setting lambda = 0 ranks terms solely by their lift

lift: the ratio of a term’s probability within a topic to its marginal probability across the corpus.

# Predict distributions

In [ ]:
common_dictionary.token2id

In [ ]:
[print(i) for i in common_dictionary.items()]

In [ ]:
len(lengths_of_docs)

In [ ]:
def testset(read_text = False):
    if read_text:
        text_library = {}
        list_of_string = []
        list_of_list_of_string = []
        lengths_of_docs_test = []

        path = "data/"
        dirs = os.listdir(path)
        for each_pdf in dirs:
            if each_pdf == 'WDR-2018-EN-LR.pdf': # our testset
                print(each_pdf)       
                with open('txt/{}.txt'.format(str(each_pdf)), 'r', encoding='utf8') as f:
                    text = f.read()
                    text_year = determine_year(each_pdf)
                    text_library[text_year] = text
            else: pass

        for i in sorted(text_library):
            print("year: {}".format(i))
            text = text_library[i]
            list_of_paragraphs = extract_para(text, lengths_of_docs_test)
            for i in list_of_paragraphs:
                if len(i) > 3:
                    list_of_list_of_string.append(preprocess(i, BIGRAMS))
                else: pass

        # Create a corpus from a list of texts
        common_dictionary_test = common_dictionary.add_documents(list_of_list_of_string)
        common_corpus_test = [common_dictionary_test.doc2bow(text) for text in list_of_list_of_string]

        common_dictionary_test.save('model/common_dictionary_test')
        with open('model/common_corpus_test_pickled', 'wb') as f:
            pickle.dump(common_corpus_test, f)
        with open('model/len_docs_test_pickled', 'wb') as f:
            pickle.dump(lengths_of_docs_test, f)
    else:        
        common_dictionary_test = Dictionary.load('model/common_dictionary_test')
        with open('model/common_corpus_test_pickled', 'rb') as f:
            common_corpus_test = pickle.load(f)
        with open('model/len_docs_test_pickled', 'rb') as f:
            lengths_of_docs_test = pickle.load(f)
    
        
        
    lda = ldamodel.LdaModel(corpus=common_corpus_test, \
                            id2word=common_dictionary_test, \
                            num_topics=num_topics, \
                            update_every=1, \
                            passes=1)
    epoch = []
    topic_list = []
    topic_imp = []

    for idx, each_topic in enumerate(lda.print_topics(num_topics=num_topics, num_words=len(common_dictionary.values()))):
        # len(common_dictionary.values()) = gets all vocab
        for each_token in each_topic[1].split('+'):
            topic_importance, token = each_token.split("*")
            topic_list.append(re.sub(r'[^A-z0-9]+', '', token))
            topic_imp.append(topic_importance)
            epoch.append(idx)
    data = {'topic_number': epoch, 'topic': topic_list, 'topic_importance': topic_imp}
    lda_df = pd.DataFrame.from_dict(data)
    
    return lda_df, common_dictionary_test

In [ ]:
testset_df, cdt = testset()
testset_df['id']= testset_df['topic'].map(cdt.token2id)
testset_df['id'] = testset_df['id'].apply(int)
testset_df['topic_importance'] = testset_df['topic_importance'].apply(float)
testset_df['epoch'] = 18
testset_df = testset_df.sort_values(['topic_number', 'id'])
testset_df.head()

In [ ]:
dtm_df['id'] = dtm_df['id'].apply(int)
dtm_df['topic_importance'] = dtm_df['topic_importance'].apply(float)
dtm_df = dtm_df.sort_values(['topic_number', 'epoch', 'id'])
dtm_df.head()

In [ ]:
len(dtm_df['epoch'].unique())

### Sklearn

In [ ]:
from sklearn.neighbors import KNeighborsRegressor
from sklearn.dummy import DummyRegressor
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import StandardScaler 
from sklearn.model_selection import GridSearchCV

In [ ]:
y_test = np.array(testset_df['topic_importance'])
y_train = np.array(dtm_df[dtm_df['epoch'] == max(dtm_df['epoch'].unique())]['topic_importance'])
X_test = np.array(dtm_df['topic_importance']).reshape(1,-1)
X_train = np.array(dtm_df[dtm_df['epoch'] != max(dtm_df['epoch'].unique())]['topic_importance']).reshape(-1,1)

print("{}\n{}\n{}\n{}".format(y_test.shape, y_train.shape, X_test.shape, X_train.shape))

In [ ]:
y_test = np.array(testset_df['topic_importance'])
y_train = np.array(dtm_df['topic_importance'])
X_test = np.array(testset_df[['id', 'topic_number', 'epoch']])
X_train = np.array(dtm_df[['id', 'topic_number', 'epoch']])

# # Scaling
# scaler = StandardScaler() 
# scaler.fit(X_train)  
# X_train = scaler.transform(X_train)  
# X_test = scaler.transform(X_test) 

# Dummy Regressor
clf_dumb = DummyRegressor()
clf_dumb.fit(X_train, y_train)

# NN Regressor
clf = KNeighborsRegressor(n_neighbors=20, n_jobs=-1)
clf.fit(X_train, y_train)

# Check error
print("dummy MSE: ", mean_squared_error(y_test, clf_dumb.predict(X_test)))
print("KNN mse: ", mean_squared_error(y_test, clf.predict(X_test)))

In [ ]:
testset_df['preds'] = clf.predict(X_test)
testset_df.head()

In [ ]:
testset_df.preds.unique()

In [ ]:
for i in (testset_df.topic_number.unique()):
    display(testset_df[testset_df['topic_number'] == i].sort_values(['topic_importance'], ascending=False)[:5])

In [ ]:
testset_df.to_csv('model/testset_df.csv')

### Pytorch
https://medium.com/dair-ai/a-simple-neural-network-from-scratch-with-pytorch-and-google-colab-c7f3830618e0

In [ ]:
import torch
import torch.tensor as tensor
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, TensorDataset

In [ ]:
class Neural_Network(nn.Module):
    def __init__(self, input_size, num_classes):
        super(Neural_Network, self).__init__()
        
        self.hidden_layer = nn.Linear(input_size, 100)
        self.dropout = nn.Dropout(p = 0.1)
        self.output = nn.Linear(100, num_classes)
        
    def forward(self, X):
        activation_output = F.tanh(self.hidden_layer(X))
        do_output = self.dropout(activation_output)
        output = F.relu(self.output(do_output))
        return output
        
    def saveWeights(self, model):
        # we will use the PyTorch internal storage functions
        torch.save(model, "NN")
        # you can reload model with all the weights and so forth with:
        # torch.load("NN")
        
    def predict(self):
        print ("Predicted data based on trained weights: ")
        print ("Input (scaled): \n" + str(xPredicted))
        print ("Output: \n" + str(self.forward(xPredicted)))

In [ ]:
def train():
    # Hyper Parameters 
    input_size = len(dtm_df)
    num_classes = len(testset_df)
    print("{}, {}".format(input_size, num_classes))
    num_epochs = 5
    batch_size = 200
    learning_rate = 0.001

    model = Neural_Network(input_size, num_classes)
    criterion = nn.CrossEntropyLoss()  
    optimizer = torch.optim.SGD(model.parameters(), lr=learning_rate)  
    device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
    model.to(device)
    
    features = tensor(dtm_df['id'].values, dtype=torch.float)
    targets = tensor(dtm_df['topic_importance'].values, dtype=torch.float)

    features_test = tensor(testset_df['id'].values, dtype=torch.float)
    targets_test = tensor(testset_df['topic_importance'].values, dtype=torch.float)

    train_dataset = TensorDataset(features, targets)
    test_dataset = TensorDataset(features_test, targets_test)

    train_loader = torch.utils.data.DataLoader(dataset=train_dataset, 
                                               batch_size=batch_size, 
                                               shuffle=True)

    test_loader = torch.utils.data.DataLoader(dataset=test_dataset, 
                                              batch_size=batch_size, 
                                              shuffle=False)

    for epoch in range(num_epochs):
        for i, (images, labels) in enumerate(train_loader):

            # Forward + Backward + Optimize
            optimizer.zero_grad()
            outputs = model(images)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            if (i+1) % 100 == 0:
                print ('Epoch: [%d/%d], Step: [%d/%d], Loss: %.4f' 
                       % (epoch+1, num_epochs, i+1, len(train_dataset)//batch_size, loss.data[0]))

    # Test the Model
    correct = 0
    total = 0
    for images, labels in test_loader:
        outputs = model(images)
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum()

    print('Accuracy of the model on the 10000 test images: %d %%' % (100 * correct / total))
    
    return

train()

# Plots

In [ ]:
def plot_specific_topic(term = 'geneva'):
    val_list = []
    for i in ldaseq.print_topic_times(topic=0, top_terms=len(common_dictionary.values())):
        for each_tup in i:
            if each_tup[0] == term:
                val_list.append(each_tup[1])
            else: pass
    plt.figure(figsize=(9, 7))
    # plt.title('Scores by group and gender')
    plt.plot(val_list)
    plt.show()

In [ ]:
plot_specific_topic('refugee')